# 03 - Interactive Viz

## Deadline

Wednesday November 8th, 2017 at 11:59PM

## Important Notes

- Make sure you push on GitHub your Notebook with all the cells already evaluated
- Note that maps do not render in a standard Github environment : you should export them to HTML and link them in your notebook.
- Remember that `.csv` is not the only data format. Though they might require additional processing, some formats provide better encoding support.
- Don't forget to add a textual description of your thought process, the assumptions you made, and the solution you plan to implement!
- Please write all your comments in English, and use meaningful variable names in your code

## Background

In this homework we will be exploring interactive visualization, which is a key ingredient of many successful data visualizations (especially when it comes to infographics).

Unemployment rates are major economic metrics and a matter of concern for governments around the world. Though its definition may seem straightforward at first glance (usually defined as the number of unemployed people divided by the active population), it can be tricky to define consistently. For example, one must define what exactly unemployed means : looking for a job ? Having declared their unemployment ? Currently without a job ? Should students or recent graduates be included ? We could also wonder what the active population is : everyone in an age category (e.g. `16-64`) ? Anyone interested by finding a job ? Though these questions may seem subtle, they can have a large impact on the interpretation of the results : `3%` unemployment doesn't mean much if we don't know who is included in this percentage. 

In this homework you will be dealing with two different datasets from the statistics offices of the European commission ([eurostat](http://ec.europa.eu/eurostat/data/database)) and the Swiss Confederation ([amstat](https://www.amstat.ch)). They provide a variety of datasets with plenty of information on many different statistics and demographics at their respective scales. Unfortunately, as is often the case is data analysis, these websites are not always straightforward to navigate. They may include a lot of obscure categories, not always be translated into your native language, have strange link structures, â€¦ Navigating this complexity is part of a data scientists' job : you will have to use a few tricks to get the right data for this homework.

For the visualization part, install [Folium](https://github.com/python-visualization/folium) (*HINT*: it is not available in your standard Anaconda environment, therefore search on the Web how to install it easily!). Folium's `README` comes with very clear examples, and links to their own iPython Notebooks -- make good use of this information. For your own convenience, in this same directory you can already find two `.topojson` files, containing the geo-coordinates of 

- European countries (*liberal definition of EU*) (`topojson/europe.topojson.json`, [source](https://github.com/leakyMirror/map-of-europe))
- Swiss cantons (`topojson/ch-cantons.topojson.json`) 

These will be used as an overlay on the Folium maps.

## Assignment

1. Go to the [eurostat](http://ec.europa.eu/eurostat/data/database) website and try to find a dataset that includes the european unemployment rates at a recent date.

   Use this data to build a [Choropleth map](https://en.wikipedia.org/wiki/Choropleth_map) which shows the unemployment rate in Europe at a country level. Think about [the colors you use](https://carto.com/academy/courses/intermediate-design/choose-colors-1/), how you decided to [split the intervals into data classes](http://gisgeography.com/choropleth-maps-data-classification/) or which interactions you could add in order to make the visualization intuitive and expressive. Compare Switzerland's unemployment rate to that of the rest of Europe.

2. Go to the [amstat](https://www.amstat.ch) website to find a dataset that includes the unemployment rates in Switzerland at a recent date.

   > *HINT* Go to the `details` tab to find the raw data you need. If you do not speak French, German or Italian, think of using free translation services to navigate your way through. 

   Use this data to build another Choropleth map, this time showing the unemployment rate at the level of swiss cantons. Again, try to make the map as expressive as possible, and comment on the trends you observe.

   The Swiss Confederation defines the rates you have just plotted as the number of people looking for a job divided by the size of the active population (scaled by 100). This is surely a valid choice, but as we discussed one could argue for a different categorization.

   Copy the map you have just created, but this time don't count in your statistics people who already have a job and are looking for a new one. How do your observations change ? You can repeat this with different choices of categories to see how selecting different metrics can lead to different interpretations of the same data.

3. Use the [amstat](https://www.amstat.ch) website again to find a dataset that includes the unemployment rates in Switzerland at recent date, this time making a distinction between *Swiss* and *foreign* workers.

   The Economic Secretary (SECO) releases [a monthly report](https://www.seco.admin.ch/seco/fr/home/Arbeit/Arbeitslosenversicherung/arbeitslosenzahlen.html) on the state of the employment market. In the latest report (September 2017), it is noted that there is a discrepancy between the unemployment rates for *foreign* (`5.1%`) and *Swiss* (`2.2%`) workers. 

   Show the difference in unemployment rates between the two categories in each canton on a Choropleth map (*hint* The easy way is to show two separate maps, but can you think of something better ?). Where are the differences most visible ? Why do you think that is ?

   Now let's refine the analysis by adding the differences between age groups. As you may have guessed it is nearly impossible to plot so many variables on a map. Make a bar plot, which is a better suited visualization tool for this type of multivariate data.

4. *BONUS*: using the map you have just built, and the geographical information contained in it, could you give a *rough estimate* of the difference in unemployment rates between the areas divided by the [RÃ¶stigraben](https://en.wikipedia.org/wiki/R%C3%B6stigraben)?

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

# Web scraping
import requests
from bs4 import BeautifulSoup
import json
import branca.colormap as cm # for color steps


# Merging names. Installation: pip install fuzzywuzzy and pip install fuzzywuzzy[speedup]
from fuzzywuzzy import fuzz
from fuzzywuzzy import process
from IPython.core import display as ICD

import folium

In [2]:
JSON_FOLDER = r'topojson/'
country_geo_path = r'topojson/europe.topojson.json'
geo_json_data_europe = json.load(open(country_geo_path))  # load coordinates for european countries
#geo_json_data_europe

In [3]:
canton_geo_path = JSON_FOLDER + r'ch-cantons.topojson.json'
geo_json_data_swiss = json.load(open(canton_geo_path))  # load coordinates for swiss cantons

In [4]:
# not really needed, just a test
m_europe = folium.Map([50,5], tiles='cartodbpositron', zoom_start=4)


## Some spare code to copy and paste

Test 
```go
from folium.plugins import FloatImage

url = ('https://raw.githubusercontent.com/SECOORA/static_assets/'
       'master/maps/img/rose.png')

m = folium.Map([-13, -38.15], zoom_start=10)

FloatImage(url, bottom=40, left=65).add_to(m)
```

Test
```go
ice_map = folium.Map(location=[-59.1759, -11.6016],
                   tiles='Mapbox Bright', zoom_start=2)

folium.GeoJson(open('antarctic_ice_edge.json'),
               name='geojson'
              ).add_to(ice_map)

folium.TopoJson(open('antarctic_ice_shelf_topo.json'),
                'objects.antarctic_ice_shelf',
                name='topojson',
               ).add_to(ice_map)

folium.LayerControl().add_to(ice_map)
ice_map
```

```go
## tuto2 (not ran)
geo_path = r'data/antarctic_ice_edge.json'
topo_path = r'data/antarctic_ice_shelf_topo.json'

ice_map = folium.Map(location=[-59.1759, -11.6016],
                     tiles='Mapbox Bright', zoom_start=2)
ice_map.geo_json(geo_path=geo_path)
ice_map.geo_json(geo_path=topo_path, topojson='objects.antarctic_ice_shelf')
ice_map.create_map()
```

In [5]:
topo_path = r'topojson/europe.topojson.json'
eu_map = folium.Map(location = [50,5], tiles='cartodbpositron', zoom_start=4)

folium.TopoJson(open(topo_path),
                'objects.europe',
                name='topojson',
               ).add_to(eu_map)

In [6]:
## use it if you want to ad more layers... here i does basically nothing i think :p
folium.LayerControl().add_to(eu_map)

In [7]:
eu_map

Test
```go
# not to be ran
state_geo_path = r'us-states.json'
geo_json_data = json.load(open(state_geo_path))

def us_election_colors(state):
    """Maps Clinton wins to blue and Trump wins to red."""
    clinton_win = state_data.loc[state_data['State'] == state, 'Winner'].values[0] > 1
    if clinton_win:
        return '#0000ff'
    else:
        return '#ff0000'
```

Test
```go
# not to be ran just for momentany understanding and copy paste
test_map = folium.Map([50,5], tiles='cartodbpositron', zoom_start=4)
folium.GeoJson(
    geo_json_data,
    style_function=lambda feature: {
        'fillColor': us_election_colors(feature['id']),
        'color' : 'black',
        'weight' : 2,
        'dashArray' : '5, 5'
        }
    ).add_to(test_map)

test_map
```

In [8]:
test_map = folium.Map([50,5], tiles='Mapbox Control Room', zoom_start=4)
folium.GeoJson(
    geo_json_data_europe,
    style_function=lambda feature: {
        'fillColor': 0,
        'color' : 'black',
        'weight' : 2,
        'dashArray' : '5, 5'
        }
    ).add_to(test_map)

test_map

Data:  **Long-term unemployment rate, % of active population aged 15-74**       _from eurostat_

link: http://ec.europa.eu/eurostat/web/products-datasets/-/tipslm70

Short Description: The long-term unemployment rate is the number of persons unemployed for 12 months or longer as a percentage of the labour force (i.e. economically active population). The unemployment rate is the number of unemployed persons as a percentage of the labour force (the total number of people employed and unemployed) based on International Labour Office (ILO) definition. Unemployed persons comprise persons aged 15 to 74 who fulfil all the three following conditions: are without work during the reference week; are available to start work within the next two weeks and have been actively seeking work in the past four weeks or have already found a job to start within the next three months. The MIP Scoreboard indicator is the three years change in percentage points. The indicative threshold is 0.5 p..
The data source is the quarterly EU Labour Force Survey (EU LFS). The survey covers the resident population in private households. 

* Name of file: tipslm70.tsv
* **:** are non available data
* **b** break in the time serie
* **e** for estimated
* **u** low relialability
* **PC** for percentage
* **PPCH** for percentage point change t/(t-3)

where:      
_A percentage point or percent point (pp) is the unit for the arithmetic difference of two percentages. For example, moving up from 40% to 44% is a 4 percentage point increase, but is an actual 10 percent increase in what is being measured._


* For data by recent months, by sex: http://ec.europa.eu/eurostat/web/products-datasets/-/teilm020
* Recent months 25-74: http://ec.europa.eu/eurostat/web/products-datasets/-/teilm022

In [9]:
# Ca race! Il y a pas la suisse ni la grèce 
# je vais en chercher un autre!

In [10]:
DATA_FOLDER = 'data/'
unemp_df1 = pd.read_csv(DATA_FOLDER + 'tipslm70.tsv' , sep='\t|,|[|]', engine='python')

#unemp_df1_PC = unemp_df1.loc[unemp_df1['unit,sex,geo\\time']=='PC_ACT,T,AT',:]
unemp_df1.head(10)
#unemp_df1.loc[unemp_df1['unit,sex,geo\\time']=='PC_ACT,T,AT',:]['unit,sex,geo\\time']

unit sex geo\time  1996   1997   1998   1999   2000    2001   2002   \
0  PC_ACT   T       AT     :      :      :      :      :       :    1.1    
1  PC_ACT   T       BE     :      :      :   4.9 b   3.8    3.2 b   3.7    
2  PC_ACT   T       BG     :      :      :      :    9.6   12.6 b  12.0    
3  PC_ACT   T       CY     :      :      :      :      :       :      :    
4  PC_ACT   T       CZ     :      :    2.0    3.2    4.2     4.2    3.7    
5  PC_ACT   T       DE     :      :      :      :      :       :      :    
6  PC_ACT   T       DK     :      :      :   1.2 b   1.0     0.9    0.9    
7  PC_ACT   T       EE     :      :      :      :   6.7 b    6.4    6.1    
8  PC_ACT   T       EL     :      :   6.0 b   6.6    6.2    5.5 b   5.3    
9  PC_ACT   T       ES  11.6   10.7    9.3    7.2    5.8    3.8 b   3.8    

   ...    2007  2008   2009   2010   2011   2012   2013  2014   2015    2016  
0  ...    1.3 b  1.0    1.2    1.2    1.2    1.2    1.3    1.5   1.7     1.9  
1  ...     3.8   3.3    3.5    4.0    3.5    3.4    3.9    4.3   4.4     4.0  
2  ...     4.1   2.9    3.0   4.7 b  6.3 b   6.8    7.4    6.9   5.6     4.5  
3  ...     0.7   0.5   0.6 b   1.3    1.6    3.6    6.1    7.7   6.8     5.8  
4  ...     2.8   2.2    2.0    3.0   2.7 b   3.0    3.0    2.7   2.4     1.7  
5  ...     4.9   3.9    3.5   3.3 b  2.8 b   2.4    2.3    2.2   2.0     1.7  
6  ...     0.6   0.5    0.6    1.5    1.8    2.1    1.8    1.7   1.7   1.4 b  
7  ...     2.3   1.7    3.7    7.6    7.1    5.5    3.8    3.3   2.4     2.1  
8  ...     4.2   3.7   3.9 b   5.7    8.8   14.5   18.5   19.5  18.2    17.0  
9  ...     1.7   2.0    4.3    7.3    8.9   11.0   13.0   12.9  11.4     9.5  

[10 rows x 24 columns]

In [11]:
tmp2 = pd.read_csv(DATA_FOLDER + 'teilm022.tsv' , sep='\t|,|[|]', engine='python')
tmp2.head()
tmp2.replace(':','nan')
tmp3 = tmp2[['age','sex','unit','geo\\time','2017M09']].loc[tmp2['sex']=='F',:] # tmp2['sex']=='F' 

#tmp3['2017M09'] = tmp3['2017M09'].astype('int')
tmp2.head() # only for females
#list(tmp3.loc[tmp3['geo\\time'] == 'BE', '2017M09'])[0]

s_adj     age sex    unit geo\time  2016M10   2016M11   2016M12  2017M01   \
0    SA  Y25-74   F  PC_ACT       AT       5.0       4.7       4.5     4.6    
1    SA  Y25-74   F  PC_ACT       BE       5.9       5.9       6.2    7.0 b   
2    SA  Y25-74   F  PC_ACT       BG       6.0       5.9       6.0     6.2    
3    SA  Y25-74   F  PC_ACT       CY      11.4      12.3      12.3    11.7    
4    SA  Y25-74   F  PC_ACT       CZ       4.0       4.0       3.7     3.9    

   2017M02   2017M03   2017M04   2017M05   2017M06  2017M07  2017M08  2017M09  
0       4.7       4.6       4.5       4.5       4.4     4.3      4.4      4.4  
1       7.3       7.2       6.6       6.2       6.0     6.1      6.0      5.9  
2       6.3       6.0       5.6       5.3       5.3     5.3      5.4      5.4  
3      11.4      11.0      10.4      10.3      10.0     9.9      9.9      9.6  
4       3.8       3.9       3.9       3.3       3.1     3.2      3.1      3.2

In [12]:
# try to make it only index and column
tmp3 = tmp3.replace(':','nan')
tmp4 = tmp3.set_index('geo\\time')['2017M09'].astype(float)
#list(tmp4.index)
tmp4.head()

geo\time
AT    4.4
BE    5.9
BG    5.4
CY    9.6
CZ    3.2
Name: 2017M09, dtype: float64

In [13]:
step = cm.StepColormap(
    ['green', 'yellow', 'red'],
    vmin=3, vmax=10,
    index=[3, 4, 8, 10],
    caption='step'
)


def unemployment_color_test(feature):
    """TEST"""
    is_present = list(tmp4.index)
    if feature['id'] not in is_present:
        return '#000000'
    else:
        return step(tmp4[feature['id']])
    




In [14]:
test_map = folium.Map([50,5], tiles='cartodbpositron', zoom_start=4)
folium.TopoJson(
    geo_json_data_europe,
    object_path='objects.europe',
    style_function=lambda feature: {
        'fillColor': unemployment_color_test(feature),
        'color' : 'black',
        'weight' : 2,
        'dashArray' : '5, 5'
        }
    ).add_to(test_map)

colormap = cm.linear.Set1.scale(0, 35).to_step(10)
step.caption = 'unemployment rate'
test_map.add_child(step)

test_map

Test
```go
# test
test_map = folium.Map([50,5], tiles='cartodbpositron', zoom_start=4)
folium.TopoJson(
    geo_json_data_europe,
    object_path='objects.europe',
    style_function=lambda feature: {
        'fillColor': step(tmp4[feature['id']]),
        'color': 'black',
        'weight': 2,
        'dashArray': '5, 5'
    }
).add_to(test_map)

test_map
```

In [15]:
a_tmp = geo_json_data_europe.copy()
def remove_country_wout_data(topojson_data,df_data_unemployment):
    out = topojson_data
    df = df_data_unemployment #just to make it more readable
    country_wout_data = []
    for i,x in enumerate(out['objects']['europe']['geometries']):
        if x['id'] not in list(df.index):
            country_wout_data.append(x)
            out['objects']['europe']['geometries'].remove(x)
    return out,country_wout_data

tmp, test = remove_country_wout_data(geo_json_data_europe,tmp4)
test

[{'arcs': [[[0, 1, 2]], [[3]], [[4]], [[5, 6, 7, 8, 9, 10], [11]]],
  'id': 'AZ',
  'properties': {'NAME': 'Azerbaijan',
   'style': {'color': 'black',
    'dashArray': '5, 5',
    'fillColor': '#000000',
    'weight': 2}},
  'type': 'MultiPolygon'},
 {'arcs': [[[-12]], [[19, -3, 20, 21, -7], [-5], [-4]]],
  'id': 'AM',
  'properties': {'NAME': 'Armenia',
   'style': {'color': 'black',
    'dashArray': '5, 5',
    'fillColor': '#000000',
    'weight': 2}},
  'type': 'MultiPolygon'},
 {'arcs': [[164,
    165,
    166,
    167,
    168,
    169,
    170,
    171,
    172,
    173,
    174,
    175,
    176,
    -10,
    177,
    -8,
    -22,
    178,
    179]],
  'id': 'GE',
  'properties': {'NAME': 'Georgia',
   'style': {'color': 'black',
    'dashArray': '5, 5',
    'fillColor': '#000000',
    'weight': 2}},
  'type': 'Polygon'},
 {'arcs': [[[231]],
   [[232]],
   [[233]],
   [[234]],
   [[235]],
   [[236]],
   [[237]],
   [[238]],
   [[239]],
   [[240]],
   [[241]],
   [[242]],
   [[

In [16]:

m = folium.Map([50,5], tiles='cartodbpositron', zoom_start=4)
folium.TopoJson(
    a_tmp,
    object_path='objects.europe',
    style_function=lambda feature: {
        'fillColor': unemployment_color_test(feature),
        'color' : 'black',
        'weight' : 2,
        'dashArray' : '5, 5'
        }
    ).add_to(m)

colormap = cm.linear.Set1.scale(0, 35).to_step(10)
step.caption = 'unemployment rate'
m.add_child(step)


In [17]:
step2 = cm.StepColormap(
    ['purple', 'yellow', 'red'],
    vmin=3, vmax=10,
    index=[3, 4, 8, 10],
    caption='step'
)

step2.caption = 'unemployment rate'
m.add_child(step2)

In [18]:
df = pd.read_csv(DATA_FOLDER + 'teilm022.tsv' , sep='\t|,|[|]', engine='python')
new_columns = []
for i,s in enumerate(df.columns):
    new_columns.append(s.strip()) # use .replace is also spaces in middle of sentence

df.columns
df = df.replace(':','nan')
date = '2017M01 '
sex = 'T'

my_count = 0
a = df[date].str.count('b').sum()
print(a)

for x in df[date]:
    if 'b' in x:
        my_count = my_count + 1
print(my_count)

df = df[['age','sex','unit','geo\\time',date]].loc[df['sex']==sex,:].astype(str)
#df = df.replace(' ','',inplace=True)
for i,x in enumerate(df[date]):
    df[date][i] = x.strip()
    x = x.replace(' ','')
    print(repr(x))
#print(repr(df))
    

    
'''new_values=[]
for x in df[date]:
    x = x.replace(' ','')
    new_values.append(x)
for x in df['geo\\time']:
    x = x.replace(' ','')'''

    
df.replace({' ': ''}, regex=True,inplace=True)

df = df.replace(':','nan')
df = df.set_index('geo\\time')[date].astype(float)

3
3
'5.0'
'6.5b'
'6.3'
'11.5'
'3.0'
'3.6'
'5.0'
'8.6'
'8.6'
'8.6'
'5.2'
'21.7'
'16.8'
'7.1'
'7.1'
'7.2'
'8.3'
'10.3'
'3.7'
'6.1'
'2.1'
'10.1'
'7.2'
'5.2'
'8.6'
'3.3'
'4.5'
'3.4'
'4.5'
'8.9'
'4.2'
'5.3'
'7.2'
'7.9'
'9.6'
'3.4'
'3.9'


ValueError: could not convert string to float: '6.5b'

In [19]:
df = pd.read_csv(DATA_FOLDER + 'teilm022.tsv' , sep='\t|,|[|]', engine='python')
df['geo\\time'][df['sex']=='F']

0       AT
1       BE
2       BG
3       CY
4       CZ
5       DE
6       DK
7       EA
8     EA18
9     EA19
10      EE
11      EL
12      ES
13    EU27
14    EU28
15      FI
16      FR
17      HR
18      HU
19      IE
20      IS
21      IT
22      LT
23      LU
24      LV
25      MT
26      NL
27      NO
28      PL
29      PT
30      RO
31      SE
32      SI
33      SK
34      UK
35      US
Name: geo\time, dtype: object

In [20]:
sex = 'F'
date = '2017M09'
df = get_unemployment_serie(sex,date)

fig1 = plt.figure(figsize=(15,6))
sns.barplot(df.index,df.sort_values())

NameError: name 'get_unemployment_serie' is not defined

In [21]:
# do one per dataset
def get_unemployment_serie(sex,date):
    """ enter desired sex and date as string
    for date: example: 2017M09 for september 2017
    """
    df = pd.read_csv(DATA_FOLDER + 'teilm022.tsv' , sep='\t|,|[|]', engine='python')
    
    new_columns = []
    for s in df.columns:
        new_columns.append(s.replace(' ','')) # use s.strip() if we dont wanna remove intermediate spaces as well
    df.columns = [new_columns]
    df = df[['geo\\time',date]].loc[df['sex']==sex,:].astype(str)
    
    '''for i,x in enumerate(df[date]):
        df[date][i] = x.strip()
        df[date][i] = x.replace(' ','')
    for i,x in enumerate(df['geo\\time']):
        df['geo\\time'][i] = x.replace(' ','')'''
    df.replace({' ': ''}, regex=True,inplace=True)
    df.replace({'b': ''}, regex=True,inplace=True)

    df = df.replace(':','nan')
    df = df.set_index('geo\\time')[date].astype(float)
    #out.values = new_values.astype(float)
    return df



def create_colormap(index = 1, min_=0, max_=10,steps=10 ):
    if index == 1:
        step = cm.StepColormap(
            ['green', 'yellow', 'red'],
            vmin=3, vmax=10,
            index=[3, 4, 8, 10],
            caption='step'
            )
    if index == 2 :
        step = cm.linear.Set1.scale(min_, max_).to_step(steps)
    return step

def unemployment_color(feature,unemployment_serie,colormap):
    """return color for countries, black if no data ':'
    depends on colormap settings"""

    if feature['id'] not in list(unemployment_serie.index):
        return '#000000'
    else:
        return colormap(unemployment_serie[feature['id']])

def get_topojson(country_geo_path):
    return json.load(open(country_geo_path))
    
def create_map (sex='T',date='2017M09'):
    topojson = get_topojson(country_geo_path) # get the topojson file
    m_serie = get_unemployment_serie(sex,date) # get the unemployment serie
    colormap = create_colormap(2,m_serie.min(),m_serie.max(),steps = 5) # create a colorfeature
    topojson,tmp = remove_country_wout_data(topojson,m_serie)
    
    
    m = folium.Map([50,5], tiles='cartodbpositron', zoom_start=4)
    folium.TopoJson(
        topojson,
        object_path='objects.europe',
        style_function=lambda feature: {
            'fillColor': unemployment_color(feature,m_serie,colormap),
            'color' : 'black',
            'weight' : 2,
            'dashArray' : '5, 5'
            }
        ).add_to(m)
    colormap.caption = 'unemployment rate'
    m.add_child(colormap)
    return m



In [50]:
topo = json.load(open(country_geo_path))#['objects']['europe']['geometries']
for element in topo:
    print(element)
    #element.pop('hours', None)
    
'''for element in data: 
    if element 
    del element['imageData']'''
topo['objects']['europe']['geometries'][0]

type
objects
arcs
transform


{'arcs': [[[0, 1, 2]], [[3]], [[4]], [[5, 6, 7, 8, 9, 10], [11]]],
 'id': 'AZ',
 'properties': {'NAME': 'Azerbaijan'},
 'type': 'MultiPolygon'}

# try to select popups

In [46]:
m = folium.Map([50,5], tiles='cartodbpositron', zoom_start=4)
rates = get_unemployment_serie('F','2017M08')

m.choropleth(geo_data=geo_json_data_europe, data=rates,
             columns=['geo\\time', '2017M08'],
             key_on='id',
             topojson= 'objects.europe',
             fill_color='BuPu', fill_opacity=0.8, line_opacity=0.9,
             legend_name='Percentage of unemployment (%)')

'''pop = folium.Map([50,5], tiles='cartodbpositron', zoom_start=4)
#for x in topo:
pop.choropleth(geo_data=topo[i],
                      key_on='id',
                      #topojson='',
                      name='topojson',
                      fill_color='autumn', fill_opacity=0.8, line_opacity=0.9
               )
pop.add_child(folium.Popup('outline Popup on GeoJSON'))
pop.add_to(m)'''

pop = folium.TopoJson(data=open(country_geo_path),
                      object_path='objects.europe',
                      key_on='id',
                      name='topojson'
               ).add_to(m)

pop.add_child(folium.Popup('outline Popup on GeoJSON'))
pop.add_to(m)

folium.LayerControl().add_to(m)
m

TypeError: __init__() got an unexpected keyword argument 'key_on'

In [47]:
from folium.plugins import TimeSliderChoropleth

ImportError: cannot import name 'TimeSliderChoropleth'

In [45]:
m = create_map(sex='T',date='2017M08')

'''pop = folium.GeoJson(
    data={
        'type': 'Polygon',
        'coordinates': [[[27, 43], [33, 43], [33, 47], [27, 47]]]
    }
)'''

pop = folium.TopoJson(data=open(country_geo_path),
                      object_path='objects.europe',
                      name='topojson'
               ).add_to(m)

pop.add_child(folium.Popup('outline Popup on GeoJSON'))
pop.add_to(m)

folium.LayerControl().add_to(m)

#m.save(os.path.join('results', 'simple_popups.html'))

m

In [24]:
from IPython.html.widgets import interact
sex_list = ['T','F','M']
date_list = ['2017M01','2017M02','2017M03','2017M04','2017M05','2017M06',\
             '2017M07','2017M08','2017M09'] # we could write the months, but would it be worth it?
m = interact(create_map, sex=sex_list, date=date_list)

/home/zampieri/anaconda3/lib/python3.6/site-packages/IPython/html.py:14: ShimWarning: The `IPython.html` package has been deprecated since IPython 4.0. You should import from `notebook` instead. `IPython.html.widgets` has moved to `ipywidgets`.
  "`IPython.html.widgets` has moved to `ipywidgets`.", ShimWarning)


interactive(children=(Dropdown(description='sex', options=('T', 'F', 'M'), value='T'), Dropdown(description='date', index=8, options=('2017M01', '2017M02', '2017M03', '2017M04', '2017M05', '2017M06', '2017M07', '2017M08', '2017M09'), value='2017M09'), Output()), _dom_classes=('widget-interact',))

In [25]:
import os
m.save(os.path.join('', 'Colormaps_3.html'))

AttributeError: 'function' object has no attribute 'save'

In [ ]:
# import swiss geometries for martino

In [ ]:
JSON_FOLDER = r'topojson/'
canton_geo_path = JSON_FOLDER + r'ch-cantons.topojson.json'
geo_json_data_swiss = json.load(open(canton_geo_path))  # load coordinates for swiss cantons
# geo_json_data_swiss['objects']['cantons']['geometries'] # for json understanding

m = folium.Map([46,6], tiles='cartodbpositron', zoom_start=7)

folium.TopoJson(
    geo_json_data_swiss,
    object_path='objects.cantons',
    style_function=lambda feature: {
        'color' : 'black',
        'weight' : 2,
        'dashArray' : '5, 5'
        }
    ).add_to(m)
m

## From now on just bullshit, do not nother to run


In [ ]:
import re

with open("map.html") as inf:
    txt = inf.read()

#Find all the markers names given by folium
markers = re.findall(r'\bmarker_\w+', txt)

for marker in markers:
   # Add the code given before to the string txt

# Save the new map
with open("new_map.html", "w") as outf:
    outf.write(txt)

In [ ]:
# not working (try for interacive plots)
for id_ in a_tmp['id']:
      folium.TopoJson(
          a_tmp,
       #feature,
          object_path='objects.europe',
        style_function=lambda feature: {
        #Put your style here
        'fillColor': '#00000',
        'color': 'black',
        'weight': 2,
        'dashArray': '5, 5'
        },        
    ).add_child(folium.Popup("put anything useful here")).add_to(test_map)
test_map

In [ ]:
from bokeh.io import show
from bokeh.models import (
    ColumnDataSource,
    HoverTool,
    LogColorMapper
)
from bokeh.palettes import Viridis6 as palette
from bokeh.plotting import figure

from bokeh.sampledata.us_counties import data as counties
from bokeh.sampledata.unemployment import data as unemployment

palette.reverse()

counties = {
    code: county for code, county in counties.items() if county["state"] == "tx"
}

county_xs = [county["lons"] for county in counties.values()]
county_ys = [county["lats"] for county in counties.values()]

county_names = [county['name'] for county in counties.values()]
county_rates = [unemployment[county_id] for county_id in counties]
color_mapper = LogColorMapper(palette=palette)

source = ColumnDataSource(data=dict(
    x=county_xs,
    y=county_ys,
    name=county_names,
    rate=county_rates,
))

TOOLS = "pan,wheel_zoom,reset,hover,save"

p = figure(
    title="Texas Unemployment, 2009", tools=TOOLS,
    x_axis_location=None, y_axis_location=None
)
p.grid.grid_line_color = None

p.patches('x', 'y', source=source,
          fill_color={'field': 'rate', 'transform': color_mapper},
          fill_alpha=0.7, line_color="white", line_width=0.5)

hover = p.select_one(HoverTool)
hover.point_policy = "follow_mouse"
hover.tooltips = [
    ("Name", "@name"),
    ("Unemployment rate)", "@rate%"),
    ("(Long, Lat)", "($x, $y)"),
]

show(p)